In [156]:
import os
import pandas as pd
import numpy as np
import math
from collections import defaultdict

In [9]:
data_dir= '/nipa/jaeho3690/7_CS229/4_Naive_Bayes/1_Data'
train_dir=data_dir+ '/ratings_train.txt'
test_dir=data_dir+ '/ratings_test.txt'

In [149]:
train= pd.read_table(train_dir)
train.drop(columns=["id"],inplace=True)

In [150]:
test = pd.read_table(test_dir)
test.drop(columns=['id'],inplace=True)

In [151]:
train.head(20)

document  label
0                                 아 더빙.. 진짜 짜증나네요 목소리      0
1                   흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2                                   너무재밓었다그래서보는것을추천한다      0
3                       교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4   사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1
5       막 걸음마 뗀 3세부터 초등학교 1학년생인 8살용영화.ㅋㅋㅋ...별반개도 아까움.      0
6                               원작의 긴장감을 제대로 살려내지못했다.      0
7   별 반개도 아깝다 욕나온다 이응경 길용우 연기생활이몇년인지..정말 발로해도 그것보단...      0
8                              액션이 없는데도 재미 있는 몇안되는 영화      1
9       왜케 평점이 낮은건데? 꽤 볼만한데.. 헐리우드식 화려함에만 너무 길들여져 있나?      1
10                                   걍인피니트가짱이다.진짜짱이다♥      1
11        볼때마다 눈물나서 죽겠다90년대의 향수자극!!허진호는 감성절제멜로의 달인이다~      1
12                울면서 손들고 횡단보도 건널때 뛰쳐나올뻔 이범수 연기 드럽게못해      0
13  담백하고 깔끔해서 좋다. 신문기사로만 보다 보면 자꾸 잊어버린다. 그들도 사람이었다...      1
14  취향은 존중한다지만 진짜 내생에 극장에서 본 영화중 가장 노잼 노감동임 스토리도 어...      0
15                                   ㄱ냥 매번 긴장되고 재밋음ㅠㅠ      1
16  참 사람들 웃긴게 바스코가 이기면 락스코라고 까고바비가 이기면 아이돌이라고 깐다.그...      1
17                 굿바이 레닌 표절인것은 이해하는데 왜 뒤로 갈수록 재미없어지냐      0
18      이건 정말 깨알 캐스팅과 질퍽하지않은 산뜻한 내용구성이 잘 버무러진 깨알일드!!♥      1
19                 약탈자를 위한 변명, 이라. 저놈들은 착한놈들 절대 아닌걸요.      1

In [155]:
train['label'].value_counts()

0    75173
1    74827
Name: label, dtype: int64

In [32]:
train=np.array(train)

In [143]:
class NaiveBayesClassifier:
    
    def __init__(self,k=0.5):
        self.k= k
        self.word_prob= []
        
    def load_corpus(self, path):
        corpus = pd.read_table(path)
        if 'id' in corpus.columns:
            corpus.drop(columns=['id'],inplace=True)
        corpus = np.array(corpus)
        return corpus
    
    def count_words(self,training_set):
        counts= defaultdict(lambda :[0,0])
        for doc, point in training_set:
            if self.is_number(doc) is False:
                words= doc.split()
                for word in words:
                    counts[word][0 if point==0 else 1]+=1
        return counts
            
    def is_number(self,s):
        try:
            float(s)
            return True
        except ValueError:
            return False
    def word_probabilities(self,counts,total_class0,total_class1,k):
        return [(w,
                 (class0+k)/(total_class0 +2*k),
                 (class1+k)/(total_class1 +2*k)) 
                for w,(class0,class1) in counts.items()]
    
    def class0_probability(self,word_probs,doc):
        docwords= doc.split()
        
        log_prob_if_class0 = log_prob_if_class1= 0.0
        for word ,prob_if_class0,prob_if_class1 in word_probs:
            #print(word,prob_if_class0,prob_if_class1)
            
            if word in docwords:
                log_prob_if_class0+= math.log(prob_if_class0)
                log_prob_if_class1+= math.log(prob_if_class1)
                
            else:

                log_prob_if_class0 += math.log(1 - prob_if_class0)
                log_prob_if_class1 += math.log(1 - prob_if_class1)
        prob_if_class0 = math.exp(log_prob_if_class0)
        prob_if_class1 = math.exp(log_prob_if_class1)
        return prob_if_class0 /(prob_if_class0 + prob_if_class1)
    
    def train(self,trainfile_path):
        training_set = self.load_corpus(trainfile_path)
        counts= self.count_words(training_set)
        
        
        total_class1 = len([1 for _, point in training_set if point ==1])
        print(total_class1)
        total_class0 = len(training_set) - total_class1
        
        
        self.word_prob=self.word_probabilities(counts,total_class0,total_class1,self.k)
        
    def classify(self,doc):
        return self.class0_probability(self.word_prob,doc)
        
        
        
        
        

In [144]:
model= NaiveBayesClassifier()

In [145]:
model.train(train_dir)

74827


In [134]:
test

document  label
0                                                    굳 ㅋ      1
1                                   GDNTOPCLASSINTHECLUB      0
2                 뭐야 이 평점들은.... 나쁘진 않지만 10점 짜리는 더더욱 아니잖아      0
3                       지루하지는 않은데 완전 막장임... 돈주고 보기에는....      0
4      3D만 아니었어도 별 다섯 개 줬을텐데.. 왜 3D로 나와서 제 심기를 불편하게 하죠??      0
...                                                  ...    ...
49995          오랜만에 평점 로긴했네ㅋㅋ 킹왕짱 쌈뽕한 영화를 만났습니다 강렬하게 육쾌함      1
49996       의지 박약들이나 하는거다 탈영은 일단 주인공 김대희 닮았고 이등병 찐따 OOOO      0
49997                 그림도 좋고 완성도도 높았지만... 보는 내내 불안하게 만든다      0
49998     절대 봐서는 안 될 영화.. 재미도 없고 기분만 잡치고.. 한 세트장에서 다 해먹네      0
49999                                         마무리는 또 왜이래      0

[50000 rows x 2 columns]

In [142]:
model.classify("졸작")

0.9770321671031783

In [49]:
model.count_words(a)

defaultdict(<function __main__.NaiveBayesClassifier.count_words.<locals>.<lambda>()>,
            {'아': [704, 500],
             '더빙..': [2, 0],
             '진짜': [3044, 2885],
             '짜증나네요': [10, 0],
             '목소리': [60, 39],
             '흠...포스터보고': [0, 1],
             '초딩영화줄....오버연기조차': [0, 1],
             '가볍지': [0, 17],
             '않구나': [1, 1],
             '너무재밓었다그래서보는것을추천한다': [1, 0],
             '교도소': [2, 2],
             '이야기구먼': [1, 0],
             '..솔직히': [1, 0],
             '재미는': [205, 84],
             '없다..평점': [1, 0],
             '조정': [8, 2],
             '사이몬페그의': [0, 1],
             '익살스런': [0, 2],
             '연기가': [250, 484],
             '돋보였던': [2, 20],
             '영화!스파이더맨에서': [0, 1],
             '늙어보이기만': [0, 1],
             '했던': [65, 70],
             '커스틴': [0, 3],
             '던스트가': [0, 1],
             '너무나도': [70, 122],
             '이뻐보였다': [0, 1],
             '막': [122, 64],
             '걸음마': [1, 0],
             '뗀': 

In [23]:
a =defaultdict(lambda :[0,0])

In [43]:
a["test"][1]+=1

In [44]:
a['test']

[2, 3]

In [26]:
print(a)

defaultdict(<function <lambda> at 0x7f072bf26d90>, {'test': [0, 0]})


In [33]:
for i,j in train:
    print(i)
    print(j)

아 더빙.. 진짜 짜증나네요 목소리
0
흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나
1
너무재밓었다그래서보는것을추천한다
0
교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정
0
사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 던스트가 너무나도 이뻐보였다
1
막 걸음마 뗀 3세부터 초등학교 1학년생인 8살용영화.ㅋㅋㅋ...별반개도 아까움.
0
원작의 긴장감을 제대로 살려내지못했다.
0
별 반개도 아깝다 욕나온다 이응경 길용우 연기생활이몇년인지..정말 발로해도 그것보단 낫겟다 납치.감금만반복반복..이드라마는 가족도없다 연기못하는사람만모엿네
0
액션이 없는데도 재미 있는 몇안되는 영화
1
왜케 평점이 낮은건데? 꽤 볼만한데.. 헐리우드식 화려함에만 너무 길들여져 있나?
1
걍인피니트가짱이다.진짜짱이다♥
1
볼때마다 눈물나서 죽겠다90년대의 향수자극!!허진호는 감성절제멜로의 달인이다~
1
울면서 손들고 횡단보도 건널때 뛰쳐나올뻔 이범수 연기 드럽게못해
0
담백하고 깔끔해서 좋다. 신문기사로만 보다 보면 자꾸 잊어버린다. 그들도 사람이었다는 것을.
1
취향은 존중한다지만 진짜 내생에 극장에서 본 영화중 가장 노잼 노감동임 스토리도 어거지고 감동도 어거지
0
ㄱ냥 매번 긴장되고 재밋음ㅠㅠ
1
참 사람들 웃긴게 바스코가 이기면 락스코라고 까고바비가 이기면 아이돌이라고 깐다.그냥 까고싶어서 안달난것처럼 보인다
1
굿바이 레닌 표절인것은 이해하는데 왜 뒤로 갈수록 재미없어지냐
0
이건 정말 깨알 캐스팅과 질퍽하지않은 산뜻한 내용구성이 잘 버무러진 깨알일드!!♥
1
약탈자를 위한 변명, 이라. 저놈들은 착한놈들 절대 아닌걸요.
1
나름 심오한 뜻도 있는 듯. 그냥 학생이 선생과 놀아나는 영화는 절대 아님
1
보면서 웃지 않는 건 불가능하다
1
재미없다 지루하고. 같은 음식 영화인데도 바베트의 만찬하고 넘 차이남....바베트의 만찬은 이야기도 있고 음식 보는재미도 있는데 ; 이건 볼게없다 음식도 별로 안나오고, 핀란드 풍경이라

조엘 슈마허 최악의 영화 차라리 배트맨과 로빈이 좋음
0
대단한 것일 줄 착각. 재미도 없고, 긴장감도 없고.
0
이영화의 유일한 미덕인 태국가요를 재조명 해주었다는데 이 별을 바친다.태국노래 cd를 사고싶어질 지경이니까...
0
나 이거 중학교때 퍼펙트 월드랑 동시상열으루 봤는데 ㅋㅋㅋ 잼있었음!!
1
굿!
1
그녀의 힘든 여정과는 달리 영화는 늘어진다.
0
남녀간 사랑, 가족간의 사랑이 아닌 다른 사랑도 얼마나 진한지 보여주는 영화
1
믿지마세요 애색긔들이 다 평점 올려논거니까
0
그래도 9.0은 넘 후하군여. 평점 7.2
0
깜찍하고 귀여운 엄지왕자,사악한 마녀로부터 마을을 지켜라
0
처음에는 좋았는데 가면 갈수록 이야기가 삼매경으로 빠지는
0
흠....나름 갠찬네요
1
낯선 섬, 낯선 타인이 완전한 사랑이 되기까지의 독특한 전이
1
13구역이라는 머리를 떼고 나왔을면 더 좋았을 것을 암튼 상반기 최고의 액션 영화다
1
결국은 세계는 이해관계에 따라 움직인다.악과 선은 없다.다 가족을 사랑하고 돈 벌고 싶어한다.
1
별루
0
좋은소재 못 살린 OO 감독. 연출만 잘 했어도 대단한 영화가 되었을텐데...쯧쯧..
0
저수지의 개폼 버젼. 참고가 아닌 표절.
0
한국남자들이여 자신을 좋아할만큼 능력이 아닌 매력과 인간으로서의 냄새를 내뿜어라. 하지만 한국에선 불가능 ㅠ조용한 분위기에서 터지는 관계씬과 특히나 코미디는 정말로 재미잇다.
1
네이든 영화 강추합니다. 수학천재 얘기라고 해서 지루할꺼라 생각했는데...감동적이구 즐겁게 봤어요. Ost두 넘 좋았구요. 알러뷰~~
1
하이틴 공포물의 대표격. 단점이라면 살인마가 하나도 안 무섭다.
0
왜만든지모르겟다.
0
똑같은스토리..혹시나했는데 역시나라는..남은스토리도 뻔하겠다는..그래서 더 안보게해줘서 고맙다는..에궁 작가님들 글쓰기 힘들텐데 기왕 힘들게쓰는거 좀 참신하게들 쓰심..왜들 지난얘기들을 습작하는지원..오늘로 끝.
0
나수윤의 발견!
1
우아하다는 말에 공감 ㅎㅎ
1
너무 배배꼬았다
0
진짜 대박 재밌음 

개인적 점수는 9점. 김희선의 재발견에 +1점. 합이 10점. 취향을 탈거 같으면서도 의외로 누구나 빠져드는 영화.
1
엄마랑 정말 재미있게 봤었지ㅎㅎ... 마지막 장면이 기차 타고 떠나는거였었나...
1
스토리가 2프로 아쉽지만 소재 선택이 좋습니다. 꼭 봐보세요
1
적당히 좀 하자...우리는 봉이 아니라구...대동강물장사도 이런 대동강물장사가 없네
0
박평식-뚜껑열린다ㅋㅋㅋ
0
배급사의 머리가 의심된다 어떻게 이게 레옹2지...
0
로버트드니로+알파치노=명화. bacause she got a great ass!! ㅋㅋㅋㅋ
1
스토리구상은좋은데 대사가탄탄하지않아
0
임권택 감독 영화를 많이 본 것은 아니지만, 이 영화 역시 구성이 탄탄하고 장면마다 상징적 의미가 묵직하고 섬세하게 들어있다.
1
이걸 2004년에 만들엇다는건 그만큼 로봇이 발전할거라 예상한거겟죠? 정말...멋지고 스토리 굿굿 재미잇기도하고... 마치 미래에일어날것만같은 느낌...?
1
자비에 돌란 영화는 본인이 게이답게 모든 연출작이 게이코드가 확실하게 들어가있음. 일반인이 봤을때 공감할만한 부분을 찾기힘들다
0
결정적인 부분은 우연에 기댄다. 허술하고 현실성 없는 추리도 문제. 심리학자가 일은 안하고 탐정놀이하는것도 문제. 사람들이 상담받으러 왔다가 사건만(?) 던져주고 가는등..'설정'을 위한 설정 때문에 어이가 없다. 직소퍼즐 같은 진부한 소품도 유치.
0
짜고치는 고스톱에 마지막 장면 진짜 허무함.ㅡㅡ
0
마동석씨가 주연도 아니고. 아역이 주연임. ㅡ.ㅡ... 마동석을 데리고.. 영화를 이렇게 만들다니..진짜 충격의 도가니임....그냥그돈으로 치킨한마리
0
감동의 전율☆
1
많은 것에 대해 배웠다. 캐리와 빅이 행복하길..♥
1
최고다 이연걸 영화 최고중의 최고..
1
인상깊은 영화였어요'가구야 공주 이야기' 노래도 영화 보고 나니 가사가 뒷이야기처럼 들렸었구요
1
코믹 호러용치고 수작인데 평점 너무 낮다
1
영화수준에 비해 평점이 지나치게 높아서 1점 ... 실제로는 5점정도? 일단 

0
영화보고처음이자마지막으로눈물흘
1
너무 뻔한거아닌가?? 별다섯개주는 애들정말 무뇌충??
0
이해가안되노
0
이거 dvd어디서구하나요?
1
최진실은 완전 얼짱에 몸짱에 매력짱이었다.
1
어느 하나 쓸데없는 장면이 없는 탄탄한 구성의 웰메이드 드라마, 본방사수 못하고 이제야 본게 안타깝다.
1
공포영화 맞니?
0
감독 죽는다...진짜....
0
내 인생 최고의 영화이자 드라마... 이 드라마를 보았던 고3 시절이 가장 행복했다
1
개구쟁이 스머프
1
bad
0
낸시 알렌 이쁘고 섹시하다
0
내인생 최고의 영화였음진짜 섬세한 감정표현과 마지막 팬텀의울음섞인 노래소리가 너무 감동적이었고돈주앙의 승리에서의 팬텀은 영화내 최고로 섹시하고환상적이었음....제라드 버틀러 짱짱맨♥♥♥♥
1
ㅎ
1
우리나라 국민도 함께 봐야 하는 감동의 영화 !
1
지금 당장 포토만 켜도 이 영화 CG를 볼수있습니다
0
울버린의 클로가 강철도 자르는 클로인데어째서 일본산 사무라이칼을 못 잘라....?
0
막장스토리따위는 커버쳐버리는 드팔마의 연출력. 그의 영화를 극장에서 보는 것이 영광. 역시 '클라스는 영원하다.'
1
굿
1
"""이 영화를 알면 간첩""이라 할정도로 민망스러운 영화"
0
기대보다 재미있었지만 여기 저기 검열의 흔적이 보여 아쉬움
0
미안해라는, 말 속에 숨겨진 전할 수 없는 소중함들.
1
너무 강하다
0
최고다~위트있는대사와 깔끔한 마무리까지~못보신분들 꼭 보세요~
1
미친아내와 미친남편 그리고 미친소녀
0
별로
0
어설펐어. 그치만 빈 디젤
0
정말 예쁘고 아름답고 사람스럽고 감동적고 말이 필요없음
1
이영화는 현대사를 배경으로한 영화입니다.
0
ㅋㅋ 이게 영화냐 ㅡㅡ 시간 버렸네
0
우리 앞에 펼쳐진 세상~은
1
내가 나비 꿈을 꾸는가 나비가 내 꿈을 꾸는 것인가
1
이완 맥그리거 조낸 귀엽다
1
재밌는데... 솔직히 1점은 아니다. 임지연 연기 잘하는건 아닌데 캐릭터랑 너무 잘어울리는듯. 이거 보고 임지연 완전 호감됨ㅋㅋ유이도 생각보다 연기 잘하고 박형식도 비주얼 

1
진짜진짜 보다보다 이렇게지겨운만화첨입니다딸램보여주려갔더만헉포스터사기입니다포스터색감이라도되면좋으려만시커한바다 우울한 대사더빙엉망임이렇게재미없을수있나요극장서 중간 애들이졸리다고난리ㅡㅡ
0
그냥 굳이지 뭐... 아니면 그리 패러디가 엄청나게 나왔겠소?
1
훌륭한 선생님과 제자들. 나도 저런 학창시절을 갖고 싶다.
1
먼지도 모르고썻다는 ..ㅋ
1
하........
0
수녀님의 모습을 볼 수 있는 유일한 영화인 듯 !
1
총을 쏘았다는데 총알이 없어. 탄피도 없어. 다쳤는데 왜 다쳤는지를 모르겠네. 개법부를 엎어버려야지 원
1
이건 영화가 아니라 TV매장에서 화질 감상용으로 틀어주는 영상이다.
0
네
1
액트오브밸러나 론서바이버 등등 네이비씰 나오는 영화 굉장히 좋아해서 일부러 찾아 봤는데.. 진짜 개 실망이다.. 헐리우드식 억지 감동..그런걸 다 떠나서 개연성이 너무 부족하다.. 민폐 모니카도 갑자기 정의의 사도가 된 브루스도 ㅋㅋ
0
스탤론 행님의 레전드 걸작이제영원히 살아 있네 졸라 재미있게잘 즐겨 봤다
1
옛날영화답지않은 즐거움
1
오, 의외로 스토리가 탄탄한데요? 저도 통크게 10점 드립니다^^
1
재밌어요 평점에 속지마시길!
1
조용하면서 자극적인 영화.정신건강에 좋지않다.에바 그린의 미모에 넋을 놓고 봤다.아들과 관계 후 아들은 자괴감에 허탈해 하고 떠난다
0
평점 왜케 높노. 잔인하고 잔인하기만한 영화. 문명이고 나발이고, 의미·메세지는 없다. 그냥 80년에 잔인한 연출을 시도한 영화일뿐. 밑도끝도 없는 상당히 불쾌한 영화.
0
별점이 왜 낮지...잼있어요!!
1
재밌따.. 웃기기도하고,
1
창작의 괴로움이 이리 돋보이리랴!
1
오랜만에 끝까지 참고 본 영화. 책을 읽지 말껄 그랬따.
0
난 이해 못하겠음 아무래도 못하겠음 전개도 안좋고 그냥 안좋음
0
이현우 때문에 다시본다... 이거 볼땐 설리랑 민호 떄문에 봤었지.
1
최고 예요 정말 감동했어요.
1
영화가 이해되지 않는다고하시는 분들, 꼭 책을 읽으시길 바랍니다.
1
오래전에 본 영화인데도 지

...

0
아프도다
1
때론 진지하게 때론 코믹하게 연출해내지만 여전히 재미가 없다!
0
뭐하자는 개짓거리여..
0
이 드라마만 틀어놓으면 잠이들어버린다주말 8시는 버리는시간
0
따뜻한 의도만 있고 스토리가 없는. 데운 빈 잔 일뿐. 배우,음악,영상이 아깝다
0
재방송통해보게되었는데..진짜재밌고훈훈해지는드라마네여!저말오랜만에미소띄면서보게되네요^^본방사수!완전좋아여^^♥♥♥
1
그린랜턴==구린랜턴
0
로맨스와 스릴러, 가족애가 잘 버무려진 영화.
1
이거같이보다가 솔로됏다.
0
참 재미없네
0
아주 재미없어요~~~~
0
재밌습니다 보는내내시간가는줄..
1
표현이 현실적이나.. 너무 늘어진다..
0
무거운 사회적 이슈를 유쾌하게 풀어내며, 보기드물게 해피앤딩으로 마무리한다.
1
왜요 이 영화덕분에 좋아하는 격투게임 나왔는데 ..오래됐지만
1
맥어보이 제발 이런영화 이영화로 마지막 이엿음 좋겠다 이영화 너무하네
0
야구의 매력도 로맨스도 다 놓쳤다.
0
인생은 고통스럽다. 또한 인간은 공수래 공수거이다. 서로 비어있는 개인이 존재할 수 있는 것은 개인과 개인 사이에 관계라는 연결끈 덕분이 아닐까.
1
이거주기도 아깝다 ㅅㅂ
0
석학의 사회학강의나 독일근현대사 강의를 듣는 듯한!
1
1보다더재밋고 웃김 ㅋㅋ 이시리즈너무맘에듬
1
영화학도들에게 굉장히 중요한 작품.
1
어렸을 때 비디오 빌려봤던 영화ㅋㅋ너무 유쾌하고 재밌게 봤땅!! 가족애도 느껴지고!
1
진짜 영화OST 너무좋아서 맨날 부르고다녓다 ㅋㅋㅋ 내생에 잊지못할 최고의영화
1
현란한 쓰레기. 올리버 왜 이랬어요...
0
러브씬이야 키스씬이야
0
too slow ...
0
재미있는데 평점이 왜?
1
이렇게 답답한내용의.영화는 제취향이 아닌거 같네요
0
너무 말이안된다....시작부터 마포구청직원탓이라..? 웃음만나온다. 지가 사기당하고 공무원이라 책임져라하는영화
0
명작 좀비영화!
1
이렇게 긴박감 없는 액션스릴러도 드물 듯!배우가 아까움. 점수 낮게 드림.
0
음악완전별루 음악좋고 두주인공의 영상이 더 들어갔으면 좋았

완전 재밌따!!!
1
ㅈ같은영화 그렇게 빨리오던 경찰 갑자기 늦게오고 엄마구하겠다고 지혼자 무턱대고 범인집 들어가고 남 훔쳐보는 변태놈을 좋아하는 여주도 이해안가고 걍 다 짜증나는영화
0
보면서도 무슨 내용인지 모르겠네요 말하는것도 웅얼거리는것도 있고 화질도 안좋고 스마트폰으로 찍은것도 아니고 참 ... 솔직히 평점 높은게 이해가 안 되네요
0
촬영기법도 좋았고 웜홀이라는 소재도 참신했고 배우들의 연기도 좋았습니다.
1
난 힘들 땐, 이 영화를 되새김질해요~~ 정말 최고!
1
클린트 이스트우드 할아버지의 영화는 가슴을울리는 무언가가있다
1
포스터에 신하균씨가?
0
최악의영화 재미도없고 감동도없고 3류 신파영화
0
여주가 신세경이 아니였다면...
0
졸작이다...특히 엔딩 참 맘에 안든다..뭐그리끝나나..
0
"와 내가 어디가서 평점 안다는데, 한여자를 썸타는 남자 3명이야기라하 지들 속사정은 그렇다치고, 막장 스토리...하아...!오토바이 불탈땐 중국산이라고 생각들었고마지막 롬(끝판왕)이 여자고수에게""너 좀 살찐거같다""하..스토리막장."
0
가슴 아파요..
1
배우 김현중의 성장하는 모습을 지켜보는 재미도 있을 것 같습니다.주,조연.. 아역들까지도 열연을 해 주니 매 회 기대하며 볼 수 있을 것 같네요^^
1
이거 딱 일본av에서 다룰 소재 딱딱 여주가 이쁘게 생겨서 보는내내 꼴린거 말고는 그냥졸작
0
모크버스터를 개봉하다니... 대단하다
0
시간많고. 돈여유된다면. 봐도 괜찮을듯^^
0
이것도 영화라고 만들었니.제레미는 겁이 많아 포경수술 안한 대학 신입생같고비노쉬는 2차성징도 못한 몸매로 숙녀행새하며 담배나 피는 중딩 같다.정신이 미성숙한 자들에게 사랑은 늘 헛될뿐.
0
소소한웃음과 애잔한 감동이 주는 아름다운 사람들의 사랑이야기, 이런류의 영화 좋다
1
다크맨1 ,프랑켄슈타인1994, 대부1 ~ 믿고보는 대작영화~
1
진심 재밌어 ㅋㅋㅋㅋㅋㅋㅋ
1
별 반개주기도 아깝다ㅡㅡ 이번시즌 왜이래 누가바도 우승은 송희진이였다 송희진이 젤 노래잘하는듯
0
별로 

일본영화 답게 오바 스럽고 괴짜 스럽지만 그안에 뜨거운 뭔가가 생겨난다... 한국영화의 고고 70 같은 느낌이 난다는... 볼 수록 정이 가는 멤버들 ㅎ
1
버려~
0
노튼의 귀여움~~
1
최진실이후로 진짜 오랫만에 진정성있는 괜챦은 여배우 발견~!!
1
재미있을것같은데개념없는오연서때문에시청률이낮지!
0
만점짜리지 뭐
1
good
1
요즘 아이들이 보면 더 좋을것 같아요^^ 추억을 느끼고 싶은 어른들도 좋을것 같구요~~암튼 재미있네요~~
1
어떤 영화든 그 가치는 10년이 넘어야 인정 받고 빛을 발하는법 그 빛을 볼수 있는 이 시대에 살아감을 감사한다
1
별점 하나도 아깝다 배우들이 너무아깝다
0
소통과 인드라망. 그것은 주인공인 바다가 선물해준 것입니다.^^
1
유치하고 억지스러운 내용전개가 너무 진부하다. 뭔가 의미심장한 메시지를 담으려 한것같지만 실상은 어린아이 상상력으로 만든 영화라고밖에 안느껴진다. 작품이 현실같이 정교할순 없지만 모순이 너무많으면 눈살을 찌뿌리게 만든다.
0
글쎄... 이젠 이런게 너무 식상해... 누구나 다 그럴거라는 생각은 금물...
0
반전이라도 있겠지 - 하면서 봤던 나는 실망실망실망.
0
생각외로 재미있는 다큐네요! 개인적으로 우리나라도 합법화가 된다면 두분의 혼인 신고서가 일등으로 처리됐으면 해요 ㅋ 검은 머리 파뿌리가 될 때까지 서로 의지 하며 행복하게 사세요^^
1
솔직히 이건 너무 심한거아냐?
0
장국영의 유약한 연기가 일품..장국영은 남창으로 나옴.
1
감독의 무능력한 연출력에 놀아난 잘생긴 두 배우들이 불쌍하네
0
내가왜 보고있나하는생각이들게하는
0
감동감동...아직도 마음이 찡하네요..실컷울었어요..효도하겠습니다..
1
방금 tv에서 봤는데 재미있다...^^ 간만에 기분이 좋아진다
1
마음이 울고 웃을 수 있는 영화가족이 내 시작이고 끝임을 알려주는 영화
1
평범한 사투리도 짜증나고 재미도 없어요.
0
압도적인 연출력, 클레멘타인의 전설은 하루만에 만들어진 것이 아니었다.
1
두근두근 하면서 완전 잼있게 봤습니다

.
1
굿
1
ㅋㅋㅋㅋ이걸보느니영구와땡칠이를 보겟다 ㅅㅂ
0
낚였네 쓰레기
0
배우들 비주얼도 좋고 호주의 멋진 배경과 어우러져 볼거리가 많은 드라마였어요.^^ 꽁배우 굳!!
1
매우재밋었어요 여자친구랑 봤는데 재밋네요
1
한국영화의 문제점? 바로 '대사'야..판에 박힌 대사가 손발 오그라들게 한다
0
나름 재밌었어요 거의 끝나갈때즈음에 카이의 다채로운표정이 귀여웠음 ㅎ
1
연출, 구성, 연기 모두 합쳐 3점이면 후한점수다.
0
최근에 대상해를 너무 잼있게 봐서 다시 복귀하나 싶었더니...역시나 넌 안돼는 돼지 쉑이였어 20편찍어서 1편성공하니 그게 명감독이냐??
0
시간이 지나도 설레이고 기억에 남는 드라마 최진실의 매력이 잘 드러난 작품
1
좋네요. 긴 여운이 남는영화
1
진짜 개쓔레귀 영화입니다 공짜로 보여준다고해도 화나는 영화임
0
평점 너무 낮네..난 재밌게 봤는데..ㅎ 개인적으로 추천
1
평점 믿고 봤다 답답해 죽는 줄.. 역시 한국 영화의 한계... 7점 정도 되나 평점조절위해 1점 줌 ..
0
주인공과 옛 약혼녀의 관계가 한국 정서에는 참 맞지 않군
0
선라이즈의 설레임부터 미드나잇의 농익음까지... 넘 현실적이어서 씁쓸하긴 하지만 18여년의 시간과 함께 세월의 무게와 가치를 느끼게 하는 이런 영화를 앞으로도 볼 수 있을까? 죽을 때까지 그들의 이야기를 계속 봤으면 하는 바람이다.
1
나도 이런 모험을해보고싶다 !
1
넘 아름다운 영화네여~
1
오! 평점 높네요. 저도 진짜 좋아하는 영화에요. 소소한 일상의 반전. 아즈키판다 짱!
1
케서린 때문에 참고 봤던 영화...
0
빈디젤 영화치고 제대로 된 영화를 본적이 없다
0
효주씨 웃는게 정말 매력있네요
1
재밌다.
1
진짜 죽입니다 ㅠㅠㅠ
1
내가사랑하는 배우 랄프 파인즈‥ 더 말이 필요없는 연기자‥
1
평범한 가족영화로 추락하고 만 속편
0
풍기는 뉘앙스는 공포호러 같아요.
0
다양한 장르를 혼합해서 독특한 영화를 만들고자한 시도는 가상하지만 이것도 저것도 아닌 괴작이 되어버렸군
0
폄하할영화는

KeyboardInterrupt: 